![Logo 1](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech1.jpg)
<div class="alert alert-block alert-info">
<h1> Komputerowe wspomaganie tłumaczenia </h1>
<h2> 6,7. <i>Preprocessing i postprocessing</i> [laboratoria]</h2> 
<h3>Rafał Jaworski (2021)</h3>
</div>

![Logo 2](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech2.jpg)

In [23]:
import re
# nawiasy w rexexp = tworzy z tego grupę. w tym przypadku ma 4 grupy 
# grupa o indexie 0 to grupa całość
# grupa o indeksie 1 to to co sformatowało się dopasowało wymachowało z pierwszą grupą

string = "aaaform1aaaahform2uadaiudform3oihdhdform2oahdoihwfform2oiadoafform11"
pattern = re.compile(r'(form1)|(form2)|(form3)')
x = pattern.finditer(string)
for xx in x:
    print(xx.group())

form1
form2
form3
form2
form2
form1


Na dzisiejszych zajęciach zajmiemy się niezwykle przydatnymi narzędziami wspomagającymi pracę tłumacza. W odróżnieniu od dotychczas poznanych, nie są one oparte na pamięci tłumaczeń, ani na słownikach. Chodzi o techniki preprocessingu i postprocessingu.

Proces tłumaczenia przeprowadzony w pełni profesjonalnie składa się z wielu faz, które angażują nie tylko tłumaczy, ale także kierowników projektu, analityków, czy korektorów. Każda z tych osób do swojej pracy może wykorzystywać system informatyczny, do którego na początku całego procesu trafiają pliki do tłumaczenia. Oznacza to, że zanim tekst źródłowy trafi do tłumacza, system ma jeszcze szansę coś w nim zmienić. A kiedy tłumacz wykona już swoją pracę, można uruchomić kolejny mechanizm, który zmodyfikuje tłumaczenie przed oddaniem go do zamawiającego. Jak się domyślamy, modyfikacje tekstu przed przekazaniem go do tłumacza nazywamy **preprocessingiem**, natomiast te dokonywane po wykonaniu tłumaczenia (ale przed zwróceniem go do klienta) nazywamy **postprocessingiem**. Terminy te, będące mało zgrabnymi kalkami z języka angielskiego, mają wersje prawdziwie polskie: przetwarzanie wstępne i końcowe. Wersje te są jednak stosowane na tyle rzadko, że mogą jedynie wprowadzić zamieszanie (co w gruncie rzeczy jest dość smutne).

Typowe operacje w fazie preprocessingu obejmują:
* identyfikację tagów xmlowych (które często są później wyświetlane w interfejsie CAT-a jako jeden niepodzielny znak)
* identyfikację segmentów, których nie należy tłumaczyć (na przykład składających się z samych liczb)

* identyfikację dat i jednostek miary w tekście źródłowym

We wszystkich tych operacjach niezwykle przydatne okazują się wyrażenia regularne.

### Ćwiczenie 1: Używając wyrażeń regularnych napisz funkcję do znajdowania wszystkich tagów XML w tekście. Funkcja powinna zwracać pozycje, na których znalazła tagi.

In [19]:
import re
def find_tags(text):
    pos = []
    regexp = r'(<([_a-zA-Z]]*[^<]*)>)|(</([_a-zA-Z][^<?!]*)>)'
    pattern = re.compile(regexp)
    tags = pattern.finditer(text)
    for tag in tags:
        pos.append(tag.span())
    return pos

In [25]:
string = "<2024.21.04| Documentation on how to connect to the database with XML: <Connection><server>Games</server><database>Call of Duty</database></Connection>"
#<Connection>
#    <server>Games</server>
#    <database>Call of Duty</database>
#</Connection>

find_tags(string)

[(71, 83), (83, 91), (96, 105), (105, 115), (127, 138), (138, 151)]

### Ćwiczenie 2: Używając wyrażeń regularnych napisz funkcję do identyfikacji segmentów, których nie należy tłumaczyć. Zastosuj wymyślone przez siebie kryteria. Funkcja is_translatable powinna zwracać True, jeśli segment powinien być przetłumaczony przez tłumacza (zwykłe zdanie). False powinno być zwrócone, kiedy segment jest nieprzetłumaczalny i powinien zostać skopiowany (np. 4.2.1.)

In [362]:
def is_translatable(text):
    # v 4.2.1 / version: 4.2.1
    # a) B) / aa) BB) / a. BB. / aa. BB. / 1. 2. / 2) 3)
    # przykłady kodu python
    # nr_indeksu (6 cyfr | z/lub bez poprzedzającego znaku 's')
    
    version = r'(^v [0-9].[0-9].?[0-9]?[0-9]?$)|(^ver(:*|.*) [0-9].[0-9].?[0-9]?[0-9]?$)'
    ol = r'(^[a-zA-z][a-zA-z]?(\)|.)$)|(^[0-9][0-9]?(\)|.)$)'
    index = r'(^s?\d{6}$)'
    pyt = r"""^```python
.*?
```$"""
    
    regexp = fr'{version}|{ol}|{index}'
    
    if re.fullmatch(regexp,text):
        return False
    elif re.fullmatch(pyt,text,re.DOTALL):
        return False
    else:
        return True


In [189]:
is_translatable("Wiedza z tego przedmiotu może się dobrze przydać przy tworzeniu systemu dialogowego")

True

In [190]:
is_translatable("Kliknij enter aby rozpocząć")

True

In [185]:
x = is_translatable("ver: 4.3.34")
y = is_translatable("v 4.3.34")

print(f"ver: 4.3.34 {x}\nv 4.3.34 {y}")

ver: 4.3.34 False
v 4.3.34 False


In [184]:
x = is_translatable("s444820")
y = is_translatable("444820")
print(f"s444820 {x}\n444820 {y}")


s444820 False
444820 False


In [187]:
a = is_translatable("a)")
b = is_translatable("II.")
c = is_translatable("1.")
d = is_translatable(r"2.")
print(f"a) {a}\nII. {b}\n1. {c}\n2. {d}")

a) False
II. False
1. False
2. False


In [188]:
ex = r"""```python
def func():
    print(HelloEarth)
func()
```"""

is_translatable(ex)

False

### Ćwiczenie 3: Używając wyrażeń regularnych napisz funkcję do identyfikacji i interpretacji 5 wybranych przez siebie formatów daty. Funkcja powinna zwracać pozycje, na których odnalazła daty oraz dzień, miesiąc i rok, które ta data reprezentuje.

In [435]:
import re

def find_dates(text):
    formats = [
        r'(\d{4}-\d{2}-\d{2})',   # YYYY-MM-DD
        r'(\d{2}-\d{2}-\d{4})',   # DD-MM-YYYY
        
        r'(\d{4}/\d{2}/\d{2})',   # YYYY/MM/DD
        r'(\d{2}/\d{2}/\d{4})',   # DD/MM/YYYY
        
        r'(\d{4}\.\d{2}\.\d{2})'  # YYYY.MM.DD
        r'(\d{2}\.\d{2}\.\d{4})', # DD.MM.YYYY
    ]

    regexp = ''
    for form in formats:
        if regexp:
            regexp += "|"+form
        else:
            regexp += form

    answer = []       
    pattern = re.compile(regexp)
    dates = pattern.finditer(text)        
            
    for date in dates:
        parts = re.split(r'[-./]', date.group())
        
        if len(parts[0]) == 4:
            y = parts[0]
            d = parts[2]
        else:
            d = parts[0]
            y = parts[2]
        m = parts[1]
            
        answer.append([date.span(),d, m, y])

    return answer


find_dates("2024-04-21 awdad qwrwe 20/22/2021 negweg qwqwd %reset 1999/01/01")

[[(0, 10), '21', '04', '2024'],
 [(23, 33), '20', '22', '2021'],
 [(54, 64), '01', '01', '1999']]

Po preprocessingu i tłumaczeniu czas na postprocessing. Ponieważ wykonywany jest on na przetłumaczonym tekście, jego głównym zadaniem jest eliminacja błędów popełnionych przez tłumacza w fazie tłumaczenia. Podczas postprocessingu najczęściej wykonuje się:
* korektę pisowni dla języka docelowego
* usuwanie błędów typograficznych z tekstu (np. wielokrotne spacje, brak spacji po przecinku)
Stanowi to bardzo ważne wsparcie dla edytorów i korektorów, czyli osób sprawdzających pracę tłumacza.

Jednak nowoczesne CAT-y potrafią coś jeszcze. Są w stanie w sprytny sposób wykorzystać kombinację pre- i postprocessingu do wyręczenia tłumacza w żmudnych i technicznych czynnościach. Wykonajmy następujące ćwiczenie:

### Ćwiczenie 4: Wykorzystując funkcję find_dates napisz funkcję do obsługi dat w tłumaczeniu. Wejściem jest segment źródłowy oraz docelowy, które zawierają daty, przy czym daty te mogą być w różnych formatach. Dodatkowym parametrem wejściowym jest nazwa oczekiwanego formatu daty w tłumaczeniu (np. "Europe", "US", "digit-dot". Funkcja najpierw sprawdza, czy liczba dat w tłumaczeniu zgadza się z liczbą dat w segmencie źródłowym oraz czy odpowiadające sobie daty wskazują na ten sam dzień. Jeśli nie, wypisywane jest stosowne ostrzeżenie. Oczekiwanym wyjściem jest segment docelowy, w którym wszystkie daty są w żądanym formacie. 

In [369]:
pip install isoweek

Defaulting to user installation because normal site-packages is not writeable
Note: you may need to restart the kernel to use updated packages.


In [426]:
from isoweek import Week
from datetime import datetime

def isoWeekNumber(date_string):
    date_object = datetime.strptime(date_string, "%Y-%m-%d")
    
    return str(date_object.isocalendar()[1])

def change_substring(text, new, start, end):
    return text[:start] + new + text[end:]

def EuropeDate(target_segmnet,dates): #YYYY-MM-DD
    for date in dates:
        target_segmnet = change_substring(target_segmnet,date[3]+"-"+date[2]+"-"+date[1],date[0][0],date[0][1])
    return target_segmnet   

def USDate(target_segmnet,dates): #MM-DD-YYYY
    for date in dates:
        target_segmnet = change_substring(target_segmnet,date[2]+"-"+date[1]+"-"+date[3],date[0][0],date[0][1])
    return target_segmnet

def tyreDOTDate(target_segmnet,dates): #WWYY (weekYear) 
    index = 0
    for date in dates:
        d = date[3]+"-"+date[2]+"-"+date[1]
        target_segmnet = change_substring(target_segmnet,isoWeekNumber(d)+date[3][2:],date[0][0]-index*6,date[0][1]-index*6)
        index += 1
    return target_segmnet


def correct_dates(source_segment, target_segment, date_format):
    ss = find_dates(source_segment)
    ts = find_dates(target_segment)
    if len(ss) != len(ts):
        return 'Błąd! Niezgodna liczba dat!'
    
    for index in range(len(ss)):
        if ss[index][1] != ts[index][1]:
            print("Rozbieżny dzień w dacie!")
            print(f"source_segment: {ss[index]}")
            print(f"target_segment: {ts[index]}")
            return
        
    if date_format == "Europe":
        return EuropeDate(target_segment,ts)
    elif date_format == "US":
        return USDate(target_segment,ts)
    elif date_format == "tyre-dot":
        return tyreDOTDate(target_segment,ts)
    else:
        return "nierozpoznawalny format rządanej daty"

source="Moje urodziny: 06/07/1999\n moje najbliższe imieniny: 2024/12/04"
target="My birthday: 06/07/1999\nmy forthcoming name day: 2024/12/04."

In [431]:
print("Europe-format\n---")
print(correct_dates(source,target,"Europe"))

Europe-format
---
My birthday: 1999-07-06
my forthcoming name day: 2024-12-04.


In [432]:
print("US-format\n---")
print(correct_dates(source,target,"US"))

US-format
---
My birthday: 07-06-1999
my forthcoming name day: 12-04-2024.


In [434]:
print("Tire-Dot-Format\n---")
print(correct_dates(source,target,"tyre-dot"))

Tire-Dot-Format
---
My birthday: 2799
my forthcoming name day: 4924.


In [433]:
# Niezgodna liczba dat
print(correct_dates(target,"My birthday: \nmy forthcoming name day: 2024/12/04","Europe")) 

Błąd! Niezgodna liczba dat!


Co jeszcze można zrobić? Zajmijmy się tagami XML. Z punktu widzenia tłumacza najlepiej byłoby, gdyby mógł przetłumaczyć segment źródłowy zawierający tagi XML na język docelowy zupełnie ignorując te tagi. Ponieważ jednak tagi muszą jakoś znaleźć się w segmencie docelowym, przydałaby się jakaś "magiczna różdżka", która przeniosłaby wszystkie tagi ze źródła do tłumaczenia na mniej więcej dobre miejsca. Spełnijmy marzenie tłumacza!

Rozważmy następujący algorytm: na wejściu mamy segment źródłowy zawierający tagi oraz segment docelowy bez tagów. Dokonujemy tokenizacji segmentu źródłowego tak, aby tagi były osobnymi tokenami. Następnie przeprowadźmy tokenizację segmentu docelowego. Gdy to jest gotowe, możemy zabrać się za przenoszenie (kopiowanie) tagów z segmentu źródłowego do docelowego.

![Transfer tagów](img/tagtransfer.png)

Gdzie w segmencie docelowym powinien trafić tag? Przede wszystkim pomiędzy tokeny - nie chcemy rozbijać słów tagami. Pytanie tylko, pomiędzy które tokeny? Jeśli sytuacja jest taka, jak powyżej, kiedy segment źródłowy i docelowy mają taką samą liczbę słów nie będących tagami, przenosimy tagi na odpowiadające pozycje w tłumaczeniu. Natomiast jeśli długość tłumaczenia jest inna niż źródła, należy obliczać te pozycje w sposób proporcjonalny - jeśli np. mamy tag w źródle na pozycji 3, a tłumaczenie jest dwa razy dłuższe niż źródło, tag powinien być przeniesiony do tłumaczenia na pozycję 6. W przypadku niecałkowitych wartości proporcji stosujemy zaokrąglenia.

### Ćwiczenie 5: Zaimplementuj opisany algorytm transferu tagów.

In [673]:
import math

def transfer_tags(source_segment, target_segment):
    regexp = r'(\s|<[^>]+>)'
    tags = []
    result = ""
    index = 0

    tokens = [token for token in re.split(regexp, source_segment) if token.strip() != ""]
    
    for token in tokens:
        if re.search(r'(<[^>]+>)', token):
            tags.append([index,token])
        if token.strip() != "":
            index += 1
            
    plain_s = re.sub(r'(<[^>]+>)', '', source_segment).split(" ")
    
    t_tokens = target_segment.split(" ")
   
    if len(plain_s) == len(t_tokens):
        for tag in tags:
            t_tokens.insert(tag[0],tag[1])
    else:
        difference = len(t_tokens)/len(plain_s)
        for tag in tags:
            t_tokens.insert(math.floor(tag[0]*difference),tag[1])
        print(f"difference: {difference}")
        
    
    for token in t_tokens:
        if len(token) > 1:
            if token[0] == "<" and token[-1] == ">" and token[1] != "/":
                result += token
            elif token[1] == "/":
                result += token
            else:
                result += token  + " "
        else:
             result += token  + " "
    
    return result.strip()

PLXML = "Cześć, jestem <b>Krystian Osiński</b> i mam <i>24</i> lata."
EN = "Hi, I'm Krystian Osiński and I'm 24 years old."
transfer_tags(PLXML,EN)

difference: 1.125


"Hi, I'm <b>Krystian Osiński </b>and I'm 24 <i>years </i>old."

In [674]:
PLXML = "Cześć, jestem <b>Krystian <i>Osiński</i></b> i mam <i>prawie 24</i> lata."
EN = "Hi, I'm Krystian Osiński and I'm almost 24 years old."
transfer_tags(PLXML,EN)

difference: 1.1111111111111112


"Hi, I'm <b>Krystian <i>Osiński </i></b>and I'm almost <i>24 years </i>old."

In [675]:
PLXML = "Lubię jeść <b>pączki</b> i pić bardzo gorącą <i>kawę</i>"
EN = "I like eating donuts and drinking very hot coffee"
transfer_tags(PLXML,EN)

difference: 1.125


'I like <b>eating </b>donuts and drinking very hot <i>coffee </i>'